# Building the apo CCR2 MSM

TICA, clustering, and model building on all the apo Anton data.

- Bryn C. Taylor
- Christopher T. Lee
- Rommie E. Amaro

In [ ]:
from __future__ import print_function
import pyemma
pyemma.__version__
import os
%pylab inline
matplotlib.rcParams.update({'font.size': 12})
import pyemma.coordinates as coor
import pyemma.msm as msm
import pyemma.plots as mplt
import numpy as np
import pickle 
import mdtraj as md

## Load coordinates and select features

In [ ]:
topfile =  '../apo_trajs/apo_proteinonly.pdb'
from glob import glob
traj_list = glob('../apo_trajs/*apo*')   # these are the simulations used in the indivudual Apo and Holo analyses notebooks
traj_list.sort()
traj_list

In [ ]:
net = [(9,168), (191,107), (274,107), (274,191), (18,261),(89, 260), (89, 228), (260, 228), (18, 67), (67, 89), 
       (67, 260), (67, 261), (19, 228), (215,50), (214,103), (214,50), (213,274), (274,50), (274,32), (274,103), (274,36), 
       (36,213)]
net

In [ ]:
# choose features to look at
feat = coor.featurizer(topfile)
feat.add_residue_mindist(residue_pairs=net)

# describe the features
feat.describe()
print(feat.dimension())

In [ ]:
# set input as features in trajectory 
inp = coor.source(traj_list, feat)

## TICA

In [ ]:
dt = .24
lag = np.int(400 / dt) # determine this from timescales v. lag time plot
tica_obj_400 = coor.tica(inp, lag=lag, kinetic_map=True, var_cutoff=0.90, reversible=True)

print('TICA Dimension with a lag of 400ns:', tica_obj_400.dimension())

In [ ]:
tica_features_lag400 = tica_obj_400.feature_TIC_correlation
np.savetxt('/msm_apo/tica_features_correlation_ticalag400.txt', tica_features_lag400)

In [ ]:
for i in range(2):
    if tica_obj_400.eigenvectors[0, i] > 0:
        tica_obj_400.eigenvectors[:, i] *= -1

In [ ]:
# all simulations
Y = tica_obj_400.get_output()
total_sim_Y = np.concatenate(Y, axis=0) 

In [ ]:
## save all 
with open('/msm_apo/Y_ticalag400.txt', 'wb') as fp:
    pickle.dump(Y, fp)
with open('/msm_apo/total_sim_Y_ticalag400.txt', 'wb') as fp:
    pickle.dump(total_sim_Y, fp)

In [ ]:
## open all 
with open('/msm_apo/Y_ticalag400.txt', 'rb') as fp:
    Y = pickle.load(fp)
with open('/msm_apo/total_sim_Y_ticalag400.txt', 'rb') as fp:
    total_sim_Y = pickle.load(fp)

## K-means clustering

In [ ]:
clustering_ticalag400 = coor.cluster_kmeans(Y, max_iter=50)
dtrajs = clustering_ticalag400.dtrajs

In [ ]:
## save all

##clustercenters
with open('/msm_apo/clustercenters_ticalag400_clustdefault_net2.txt', 'wb') as fp:
    pickle.dump(clustering_ticalag400.clustercenters, fp)
    
##dtrajs
with open('/msm_apo/dtrajs_ticalag400_clustdefault.txt', 'wb') as fp:
    pickle.dump(dtrajs, fp)

In [ ]:
## open all

## clustercenters
with open('/msm_apo/clustercenters_ticalag400_clustdefault_net2.txt', 'rb') as fp:
    clustering_apo_clustercenters = pickle.load(fp)

## dtrajs   
with open('/msm_apo/dtrajs_ticalag400_clustdefault.txt', 'rb') as fp:
    dtrajs_apo = pickle.load(fp)

In [ ]:
plt.figure(figsize=(12,9), dpi=120)
plt.title('Free Energy and Clusters of CCR2 Apo \nProjected in tICA Coordinate Space', fontsize=16)

plt.subplot(321)
plt.xlabel('tIC 0', fontsize=14)
plt.ylabel('tIC 1', fontsize=14)

_, ax = mplt.plot_free_energy(total_sim_Y[:, 0], total_sim_Y[:, 1])
ax.scatter(clustering_apo_clustercenters[:,0], clustering_apo_clustercenters[:,1], color='white', s=10)


plt.subplot(322)
#plt.title('Free Energy of CCR2 Apo \nProjected in the First Two tICA Coordinates', fontsize=16)
plt.xlabel('tIC 1', fontsize=14)
plt.ylabel('tIC 2', fontsize=14)

_, ax = mplt.plot_free_energy(total_sim_Y[:, 1], total_sim_Y[:, 2])
ax.scatter(clustering_apo_clustercenters[:,1], clustering_apo_clustercenters[:,2], color='white', s=10)
#ax.scatter(clustering_tot_clustercenters[:,1], clustering_tot_clustercenters[:,2], color = 'cyan', s=5)


plt.subplot(323)
#plt.title('Free Energy of CCR2 Apo \nProjected in the First Two tICA Coordinates', fontsize=16)
plt.xlabel('tIC 0', fontsize=14)
plt.ylabel('tIC 2', fontsize=14)

_, ax = mplt.plot_free_energy(total_sim_Y[:, 0], total_sim_Y[:, 2])
ax.scatter(clustering_apo_clustercenters[:,0], clustering_apo_clustercenters[:,2], color='white', s=10)
#ax.scatter(clustering_tot_clustercenters[:,0], clustering_tot_clustercenters[:,2], color = 'cyan', s=5)


plt.subplot(324)
#plt.title('Free Energy of CCR2 Apo \nProjected in the First Two tICA Coordinates', fontsize=16)
plt.xlabel('tIC 0', fontsize=14)
plt.ylabel('tIC 3', fontsize=14)

_, ax = mplt.plot_free_energy(total_sim_Y[:, 0], total_sim_Y[:, 3])
ax.scatter(clustering_apo_clustercenters[:,0], clustering_apo_clustercenters[:,3], color='white', s=10)
#ax.scatter(clustering_tot_clustercenters[:,0], clustering_tot_clustercenters[:,3], color = 'cyan', s=5)


plt.subplot(325)
#plt.title('Free Energy of CCR2 Apo \nProjected in the First Two tICA Coordinates', fontsize=16)
plt.xlabel('tIC 1', fontsize=14)
plt.ylabel('tIC 3', fontsize=14)

_, ax = mplt.plot_free_energy(total_sim_Y[:, 1], total_sim_Y[:, 3])
ax.scatter(clustering_apo_clustercenters[:,1], clustering_apo_clustercenters[:,3], color='white', s=10)
#ax.scatter(clustering_tot_clustercenters[:,1], clustering_tot_clustercenters[:,3], color = 'cyan', s=5)


plt.subplot(326)
#plt.title('Free Energy of CCR2 Apo \nProjected in the First Two tICA Coordinates', fontsize=16)
plt.xlabel('tIC 2', fontsize=14)
plt.ylabel('tIC 3', fontsize=14)

_, ax = mplt.plot_free_energy(total_sim_Y[:, 2], total_sim_Y[:, 3])
ax.scatter(clustering_apo_clustercenters[:,2], clustering_apo_clustercenters[:,3], color='white', s=10)
#ax.scatter(clustering_tot_clustercenters[:,2], clustering_tot_clustercenters[:,3], color = 'cyan', s=5)


plt.tight_layout()
#plt.savefig('/msm_apo/images/01_clustering_ticalag400_FE.png')
plt.show()

In [ ]:
plt.figure(figsize=(12,9), dpi=300)
plt.title('Free Energy and Clusters of CCR2 Apo \nProjected in tICA Coordinate Space', fontsize=16)

plt.xlabel('tIC 0', fontsize=14)
plt.ylabel('tIC 1', fontsize=14)

_, ax = mplt.plot_free_energy(total_sim_Y[:, 0], total_sim_Y[:, 1])
ax.scatter(clustering_apo_clustercenters[:,0], clustering_apo_clustercenters[:,1], color='white', s=10)

#plt.savefig('/msm_apo/images/01_clustering_ticalag400_FE_network_tic01.png')

## Implied Timescale Plots

In [ ]:
its_apo_bayes = msm.its(dtrajs_apo, errors='bayes')

In [ ]:
plt.figure(figsize=(12,9), dpi=300)

mplt.plot_implied_timescales(its_apo_bayes, units=r'$ns$', nits=10, linewidth=2, dt=dt)
plt.title('Implied Timescale Plot with Errors: Apo Data')
#plt.savefig('/msm_apo/its_bayes_ns.png')

## Markov Model

In [ ]:
dt =.24
msm_lag = 60 
M_apo = msm.estimate_markov_model(dtrajs_apo, msm_lag, reversible=True)
print('fraction of states used = ', M_apo.active_state_fraction)
print('fraction of counts used = ', M_apo.active_count_fraction)

In [ ]:
dt =.24
msm_lag = 60 
M_apo_60_bayes = msm.bayesian_markov_model(dtrajs_apo, msm_lag, reversible=True)
print('fraction of states used = ', M_apo_60_bayes.active_state_fraction)
print('fraction of counts used = ', M_apo_60_bayes.active_count_fraction)

In [ ]:
#save as
with open('/msm_apo/M_apo_emm_ticalag400ns_msmlag60steps.txt', 'wb') as fp:
    pickle.dump(M_apo, fp)

## CK Test

In [ ]:
cktest6 = M_apo_60_bayes.cktest(6, err_est=True, mlags=5)
mplt.plot_cktest(cktest6, figsize=(24,24), layout=(2,2), padding_top=0.1, y01=False, padding_between=0.3, units='steps')

## HMM

In [ ]:
with open ('/msm_apo/M_apo_emm_ticalag400ns_msmlag60steps.txt', 'rb') as fp:
    M_apo_60 = pickle.load(fp, encoding='latin1')
with open('/msm_apo/total_sim_Y_ticalag400.txt', 'rb') as fp:
    total_sim_Y = pickle.load(fp, encoding='latin1')

In [ ]:
nhidden=6

estimator = MaximumLikelihoodHMSM(lag=M_apo_60.lagtime, 
                                  nstates=nhidden, 
                                  msm_init=M_apo_60, 
                                  reversible=M_apo_60.reversible,
                                  dt_traj=M_apo_60.dt_traj,
                                  mincount_connectivity=0
                                 )
estimator.estimate(M_apo_60.discrete_trajectories_full)
hmm = estimator.model

In [ ]:
rates = hmm.P/14.4*1e6 # 1/ms
print("Scaled Rates in 1/ms")
print(np.array2string(rates, precision=2))
print("Probabilities")
print(np.array2string(hmm.P, precision=2))
mplt.plot_markov_model(hmm, minflux=1e-25, arrow_labels=rates, arrow_label_format='%10.5f')

#rates are probability over lag time

## Plot FE + Macrostates

In [ ]:
proj_Y = total_sim_Y[:,[0,1]]

In [ ]:
metastable_hmm_traj = [hmm.metastable_assignments[traj[:]] for traj in M_apo_60.discrete_trajectories_full]
metastable_assign = np.concatenate(metastable_hmm_traj, axis=0)

In [ ]:
counts = np.zeros(nhidden)
macroCenters = np.zeros((nhidden,2))
for i in np.arange(0,len(proj_Y)):
    state = metastable_assign[i]
    counts[state] += 1
    macroCenters[state] += proj_Y[i]
macroCenters = macroCenters / counts[:,None]

In [ ]:
fig, ax = mplt.plot_free_energy(total_sim_Y[:, 0], total_sim_Y[:, 1], 
                                kT=0.592172822, 
                                cbar_label='Free Energy (kcal/mol)',
                                avoid_zero_count=True
                               )
fig.set_size_inches((12,9))
ax.set_title('''CCR2 Apo Macrostates''', fontsize=16)
ax.set_ylabel('TIC 0', fontsize=14)
ax.set_xlabel('TIC 1', fontsize=14)

ax.scatter(macroCenters[:,0], macroCenters[:,1], marker='*', s=500, c='w')

In [ ]:
print(np.array2string(macroCenters))

### Timescales

In [ ]:
M_apo_60.timescales(10)/1000

In [ ]:
hmm.timescales()/1000

## Make FE plot with all clusters in HMM states

In [ ]:
# clustercenters
with open('msm_apo/clustercenters_ticalag400_clustdefault_net2.txt', 'rb') as fp:
    clustering_apo_clustercenters = pickle.load(fp, encoding='latin1')

In [ ]:
state0 = hmm.metastable_sets[0]
state1 = hmm.metastable_sets[1]
state2 = hmm.metastable_sets[2]
state3 = hmm.metastable_sets[3]
state4 = hmm.metastable_sets[4]
state5 = hmm.metastable_sets[5]

print(len(state0))
print(len(state1))
print(len(state2))
print(len(state3))
print(len(state4))
print(len(state5))

In [ ]:
fig, ax, misc = mplt.plot_free_energy(total_sim_Y[:, 0], total_sim_Y[:, 1], 
                                kT=0.592172822, 
                                cbar_label='Free Energy (kcal/mol)',
                                avoid_zero_count=True,
                                legacy=False
                               )
fig.set_size_inches((12,9))
fig.set_dpi(300)
# ax.set_title('''Apo''', fontsize=16)
ax.set_ylabel('Apo TIC 1', fontsize=36)
ax.set_xlabel('Apo TIC 0', fontsize=36)
misc['cbar'].ax.tick_params(labelsize=36)
misc['cbar'].set_label('Free Energy (kcal/mol)',fontsize=36)

plt.tick_params(axis='both', which='major', labelsize=36)

alpha=.8
for k in range(100):
    ax.plot(clustering_apo_clustercenters[state0[k],0], clustering_apo_clustercenters[state0[k],1], linewidth=20, color='white', marker='o', markersize=10, alpha=alpha)
for k in range(202):
    ax.plot(clustering_apo_clustercenters[state1[k],0], clustering_apo_clustercenters[state1[k],1], linewidth=20, color='red', marker='o', markersize=10, alpha=alpha)
for k in range(66):
    ax.plot(clustering_apo_clustercenters[state2[k],0], clustering_apo_clustercenters[state2[k],1], linewidth=20, color='yellow', marker='o', markersize=10, alpha=alpha)    
for k in range(58):
    ax.plot(clustering_apo_clustercenters[state3[k],0], clustering_apo_clustercenters[state3[k],1], linewidth=20, color='cyan', marker='o', markersize=10, alpha=alpha)   
for k in range(77):
    ax.plot(clustering_apo_clustercenters[state4[k],0], clustering_apo_clustercenters[state4[k],1], linewidth=20, color='grey', marker='o', markersize=10, alpha=alpha)    
for k in range(162):
    ax.plot(clustering_apo_clustercenters[state5[k],0], clustering_apo_clustercenters[state5[k],1], linewidth=20, color='purple', marker='o', markersize=10, alpha=alpha)


ax.scatter(macroCenters[0,0], macroCenters[0,1], marker='o', s=1600, c='white', linewidths=2, edgecolors='black', zorder=99)
ax.scatter(macroCenters[1,0], macroCenters[1,1], marker='o', s=1600, c='red', linewidths=2, edgecolors='black', zorder=99)
ax.scatter(macroCenters[2,0], macroCenters[2,1], marker='o', s=1600, c='yellow', linewidths=2, edgecolors='black', zorder=99)
ax.scatter(macroCenters[3,0], macroCenters[3,1], marker='o', s=1600, c='cyan', linewidths=2, edgecolors='black', zorder=99)
ax.scatter(macroCenters[4,0], macroCenters[4,1], marker='o', s=1600, c='grey', linewidths=2, edgecolors='black', zorder=99)
ax.scatter(macroCenters[5,0], macroCenters[5,1], marker='o', s=1600, c='purple', linewidths=2, edgecolors='black', zorder=99)

#fig.savefig('apo_hmm.eps', dpi=300, format='eps')
